# Question & Answer System
by ES

import:

In [20]:
%matplotlib inline

import numpy as np
import matplotlib.pyplot as plt
import matplotlib.ticker as ticker
import urllib
import sys
import os
import zipfile
import tarfile
import json 
import hashlib
import re
import itertools
import gensim
import string
import math
import nltk
import random
import csv
import io
import spacy
import scipy
import string
from gensim.summarization import bm25
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import TruncatedSVD
from importlib import reload
from collections import Counter
from nltk import pos_tag, word_tokenize
from nltk.tree import Tree
from nltk.corpus import wordnet as wn
from nltk.corpus import stopwords

Open and load files:

In [2]:
with open('training.json','r') as f:
    training = json.load(f)

with open('documents.json','r') as f:
    documents = json.load(f)

with open('devel.json','r') as f:
    develop = json.load(f)
    
with open('testing.json','r') as f:
    testing = json.load(f)

TEXT SIMILARITY
Use bm25 to calculate the similarity between question and each paragraph in the target document. Get the paragraph with highest score.
For test set, return the question and paragraph.
For training/develop set, return the index of paragraph, index of right paragraph, and right answer as well

In [26]:
lemmatizer = nltk.stem.wordnet.WordNetLemmatizer()
def lemmatize(word):
    lemma = lemmatizer.lemmatize(word,'v')
    if lemma == word:
        lemma = lemmatizer.lemmatize(word,'n')
    return lemma

def wordPreprocess(word_list):
    stopWords = set(stopwords.words('english'))
    word_list_preprocessed = []
    for word in word_list:
        word_processed = lemmatize(word.lower())
        if word_processed not in stopWords and word_processed not in string.punctuation:
            word_list_preprocessed.append(word_processed)
    return word_list_preprocessed

documents_dict = {}
t = str(len(documents))
num = 0
for doc in documents:
    sys.stdout.write(('getting documents dict: '+'{0}/'+t+'\r').format(num + 1))
    sys.stdout.flush()
    para_list = []
    for para in doc["text"]:
        word_list = wordPreprocess(word_tokenize(para))
        print(word_list)
        para_list.append(word_list)
    documents_dict[doc["docid"]]=para_list
    num+=1

['first', 'recognize', '1900', 'max', 'planck', 'originally', 'proportionality', 'constant', 'minimal', 'increment', 'energy', 'e', 'hypothetical', 'electrically', 'charge', 'oscillator', 'cavity', 'contain', 'black', 'body', 'radiation', 'frequency', 'f', 'associate', 'electromagnetic', 'wave', '1905', 'value', 'e', 'minimal', 'energy', 'increment', 'hypothetical', 'oscillator', 'theoretically', 'associate', 'einstein', '``', 'quantum', "''", 'minimal', 'element', 'energy', 'electromagnetic', 'wave', 'light', 'quantum', 'behave', 'respect', 'electrically', 'neutral', 'particle', 'oppose', 'electromagnetic', 'wave', 'eventually', 'call', 'photon']
['classical', 'statistical', 'mechanic', 'require', 'existence', 'h', 'define', 'value', 'eventually', 'follow', 'upon', 'planck', "'s", 'discovery', 'recognize', 'physical', 'action', 'take', 'arbitrary', 'value', 'instead', 'must', 'multiple', 'small', 'quantity', '``', 'quantum', 'action', "''", 'call', 'planck', 'constant', 'classical', '

['bohr', 'also', 'introduce', 'quantity', 'know', 'reduce', 'planck', 'constant', 'quantum', 'angular', 'momentum', 'first', 'bohr', 'think', 'angular', 'momentum', 'electron', 'atom', 'prove', 'incorrect', 'despite', 'development', 'sommerfeld', 'others', 'accurate', 'description', 'electron', 'angular', 'momentum', 'prove', 'beyond', 'bohr', 'model', 'correct', 'quantization', 'rule', 'electron', '–', 'energy', 'reduce', 'bohr', 'model', 'equation', 'case', 'hydrogen', 'atom', '–', 'give', 'heisenberg', "'s", 'matrix', 'mechanic', '1925', 'schrödinger', 'wave', 'equation', '1926', 'reduce', 'planck', 'constant', 'remain', 'fundamental', 'quantum', 'angular', 'momentum', 'modern', 'term', 'j', 'total', 'angular', 'momentum', 'system', 'rotational', 'invariance', 'jz', 'angular', 'momentum', 'measure', 'along', 'give', 'direction', 'quantity', 'take', 'value']
['uncertainty', 'give', 'standard', 'deviation', 'measure', 'value', 'expect', 'value', 'number', 'pair', 'physically', 'measur

['legal', 'process', 'change', 'definition', 'kilogram', 'already', 'underway', 'decide', 'final', 'decision', 'would', 'make', 'next', 'meet', 'general', 'conference', 'weight', 'measure', '2011', 'detail', 'information', 'see', 'kilogram', 'definition', 'planck', 'constant', 'lead', 'contender', 'form', 'basis', 'new', 'definition', 'although', 'one', 'possible', 'new', 'definition', 'include', '``', 'mass', 'body', 'rest', 'whose', 'equivalent', 'energy', 'equal', 'energy', 'photon', 'whose', 'frequency', 'sum', '7050135639273999999♠135639274×1042', 'hz', "''", 'simply', '``', 'kilogram', 'define', 'planck', 'constant', 'equal', '6966662606895999999♠6.62606896×10−34', 'j⋅s', "''"]
['public', 'policy', 'political', 'leadership', 'help', '``', 'level', 'play', 'field', "''", 'drive', 'wider', 'acceptance', 'renewable', 'energy', 'technology', 'country', 'germany', 'denmark', 'spain', 'lead', 'way', 'implement', 'innovative', 'policy', 'drive', 'growth', 'past', 'decade', '2014', 'germ

['hydropower', 'produce', '150', 'country', 'asia-pacific', 'region', 'generate', '32', 'percent', 'global', 'hydropower', '2010', 'china', 'largest', 'hydroelectricity', 'producer', '721', 'terawatt-hours', 'production', '2010', 'represent', 'around', '17', 'percent', 'domestic', 'electricity', 'use', 'three', 'hydroelectricity', 'plant', 'larger', '10', 'gw', 'three', 'gorge', 'dam', 'china', 'itaipu', 'dam', 'across', 'brazil/paraguay', 'border', 'guri', 'dam', 'venezuela', 'cost', 'hydroelectricity', 'low', 'make', 'competitive', 'source', 'renewable', 'electricity', 'average', 'cost', 'electricity', 'hydro', 'plant', 'larger', '10', 'megawatt', '3', '5', 'u.s.', 'cent', 'per', 'kilowatt-hour']
['geothermal', 'power', 'capacity', 'grow', 'around', '1', 'gw', '1975', 'almost', '10', 'gw', '2008', 'unite', 'state', 'world', 'leader', 'term', 'instal', 'capacity', 'represent', '3.1', 'gw', 'country', 'significant', 'instal', 'capacity', 'include', 'philippine', '1.9', 'gw', 'indonesia

['pv', 'industry', 'see', 'drop', 'module', 'price', 'since', '2008', 'late', '2011', 'factory-gate', 'price', 'crystalline-silicon', 'photovoltaic', 'module', 'drop', '1.00/w', 'mark', '1.00/w', 'instal', 'cost', 'often', 'regard', 'pv', 'industry', 'mark', 'achievement', 'grid', 'parity', 'pv', 'reduction', 'take', 'many', 'stakeholder', 'include', 'industry', 'analyst', 'surprise', 'perception', 'current', 'solar', 'power', 'economics', 'often', 'lag', 'behind', 'reality', 'stakeholder', 'still', 'perspective', 'solar', 'pv', 'remain', 'costly', 'unsubsidized', 'basis', 'compete', 'conventional', 'generation', 'option', 'yet', 'technological', 'advancement', 'manufacture', 'process', 'improvement', 'industry', 're-structuring', 'mean', 'price', 'reduction', 'likely', 'come', 'year']
['many', 'energy', 'market', 'institution', 'policy', 'develop', 'support', 'production', 'use', 'fossil', 'fuel', 'newer', 'cleaner', 'technology', 'may', 'offer', 'social', 'environmental', 'benefit', 

...

['education', 'israel', 'highly', 'value', 'national', 'culture', 'historical', 'value', 'date', 'back', 'ancient', 'israel', 'view', 'one', 'fundamental', 'block', 'ancient', 'israelite', 'life', 'israeli', 'culture', 'view', 'higher', 'education', 'key', 'higher', 'mobility', 'socioeconomic', 'status', 'israeli', 'society', 'emphasis', 'education', 'within', 'israeli', 'society', 'go', 'gulf', 'within', 'jewish', 'diaspora', 'renaissance', 'enlightenment', 'movement', 'way', 'root', 'zionism', '1880s', 'jewish', 'community', 'levant', 'first', 'introduce', 'compulsory', 'education', 'organize', 'community', 'le', 'parent', 'responsible', 'education', 'next', 'generation', 'jew', 'contemporary', 'jewish', 'culture', "'s", 'strong', 'emphasis', 'promotion', 'scholarship', 'learn', 'strong', 'propensity', 'promote', 'cultivation', 'intellectual', 'pursuit', 'well', 'nation', 'high', 'university', 'educational', 'attainment', 'rate', 'exemplify', 'highly', 'israeli', 'society', 'value', 

['statistical', 'purpose', 'country', 'divide', 'three', 'metropolitan', 'area', 'tel', 'aviv', 'metropolitan', 'area', 'population', '3,206,400', 'haifa', 'metropolitan', 'area', 'population', '1,021,000', 'beer', 'sheva', 'metropolitan', 'area', 'population', '559,700', 'israel', "'s", 'largest', 'municipality', 'population', 'area', 'jerusalem', '773,800', 'resident', 'area', '126', 'square', 'kilometre', '49', 'sq', 'mi', '2009', 'israeli', 'government', 'statistic', 'jerusalem', 'include', 'population', 'area', 'east', 'jerusalem', 'widely', 'recognize', 'part', 'palestinian', 'territory', 'israeli', 'occupation', 'tel', 'aviv', 'haifa', 'rishon', 'lezion', 'rank', 'israel', "'s", 'next', 'populous', 'city', 'population', '393,900', '265,600', '227,600', 'respectively']
['since', 'israel', "'s", 'capture', 'territory', 'israeli', 'settlement', 'military', 'installation', 'build', 'within', 'israel', 'apply', 'civilian', 'law', 'golan', 'height', 'east', 'jerusalem', 'grant', 'inha

['although', 'turkey', 'israel', 'establish', 'full', 'diplomatic', 'relation', '1991', 'turkey', 'cooperate', 'state', 'since', 'recognition', 'israel', '1949', 'turkey', "'s", 'tie', 'muslim-majority', 'nation', 'region', 'time', 'result', 'pressure', 'arab', 'muslim', 'state', 'temper', 'relationship', 'israel', 'relation', 'turkey', 'israel', 'take', 'downturn', '2008–09', 'gaza', 'war', 'israel', "'s", 'raid', 'gaza', 'flotilla', 'ihh', 'organize', 'flotilla', 'turkish', 'charity', 'challenge', 'tie', 'hamas', 'al-qaeda', 'relation', 'israel', 'greece', 'improve', 'since', '1995', 'due', 'decline', 'israeli-turkish', 'relation', 'two', 'country', 'defense', 'cooperation', 'agreement', '2010', 'israeli', 'air', 'force', 'host', 'greece', '’', 'hellenic', 'air', 'force', 'joint', 'exercise', 'uvda', 'base', 'israel', 'second', 'largest', 'importer', 'greek', 'product', 'middle', 'east', 'joint', 'cyprus-israel', 'oil', 'gas', 'exploration', 'center', 'leviathan', 'gas', 'field', 'im

['israel', 'consider', 'advance', 'country', 'southwest', 'asia', 'middle', 'east', 'economic', 'industrial', 'development', 'israel', "'s", 'quality', 'university', 'education', 'establishment', 'highly', 'motivate', 'educate', 'populace', 'largely', 'responsible', 'spur', 'country', "'s", 'high', 'technology', 'boom', 'rapid', 'economic', 'development', '2010', 'join', 'oecd', 'country', 'rank', '3rd', 'region', '38th', 'worldwide', 'world', 'bank', "'s", 'ease', 'business', 'index', 'well', 'world', 'economic', 'forum', "'s", 'global', 'competitiveness', 'report', 'second-largest', 'number', 'startup', 'company', 'world', 'unite', 'state', 'largest', 'number', 'nasdaq-listed', 'company', 'outside', 'north', 'america']
['despite', 'limit', 'natural', 'resource', 'intensive', 'development', 'agricultural', 'industrial', 'sector', 'past', 'decade', 'make', 'israel', 'largely', 'self-sufficient', 'food', 'production', 'apart', 'grain', 'beef', 'import', 'israel', 'total', '77.59', 'bill

KeyboardInterrupt: 

In [23]:
develop_data = []
t = str(len(develop))
num = 0
for question in develop:
    sys.stdout.write(('getting develop data: '+'{0}/'+t+'\r').format(num + 1))
    sys.stdout.flush()
#     print(documents_dict[question["docid"]])
    bm25Model = bm25.BM25(documents_dict[question["docid"]])
    average_idf = sum(map(lambda k: float(bm25Model.idf[k]), bm25Model.idf.keys())) / len(bm25Model.idf.keys())
    scores = bm25Model.get_scores(wordPreprocess(word_tokenize(question["question"])),average_idf)
    idx = scores.index(max(scores))
    develop_data.append((question["question"],documents[question["docid"]]["text"][idx],idx,question["answer_paragraph"],question["text"]))
    num+=1

In [24]:
# test_data = []
# t = str(len(testing))
# num = 0
# for question in testing:
#     sys.stdout.write(('getting develop data: '+'{0}/'+t+'\r').format(num + 1))
#     sys.stdout.flush()
#     bm25Model = bm25.BM25(documents_dict[question["docid"]])
#     average_idf = sum(map(lambda k: float(bm25Model.idf[k]), bm25Model.idf.keys())) / len(bm25Model.idf.keys())
#     scores = bm25Model.get_scores(word_tokenize(question["question"]),average_idf)
#     idx = scores.index(max(scores))
#     test_data.append((question["question"],documents[question["docid"]]["text"][idx],idx))
#     num+=1

Evaluate function:
print the acurate of similarity part

In [25]:
def tfidfAcurate(data_list):
    data_count = 0
    correct_count = 0
    for data in data_list:
#         print(data)
        data_count+=1
#         print(data[2],data[3])
        if data[2]==data[3]:
            correct_count +=1
    return float(correct_count)/data_count

print(tfidfAcurate(develop_data))

0.7859218598643849


Get Answer:

In [ ]:
def getEntity(sentence):
    ## spacy
    nlp = spacy.load('en_core_web_sm')
    doc = nlp(sentence)
    return doc.ents

def getTextByLabel(entity,label_list):
    answer_list = []
    for ent in entity:
        label = ent.label_
        if label in label_list:
            answer_list.append(ent.text)
    return answer_list

def getAnswer(data_list):
    t = str(len(data_list))
    now = 0
    answer=[]
    id_num = 0
    count = [0,0,[0,0,0],[0,0,0,0],0,[0,0,0,0],0]
    useList = [0,0]
    for data in data_list:
        sys.stdout.write(('{0}/'+t+'\r').format(id_num + 1))
        sys.stdout.flush()
        paragraph_entity = getEntity(data[1])
        answer_list = list()
        
        if bool(re.search('who',data[0],re.IGNORECASE)):
            count[0]+=1
            answer_list = getTextByLabel(paragraph_entity,["PERSON","NORP","ORG"])
        elif bool(re.search('where',data[0],re.IGNORECASE)):
            count[1]+=1
            answer_list = getTextByLabel(paragraph_entity,["FACILITY","GPE","LOC"])
        elif bool(re.search('what',data[0],re.IGNORECASE)):
            if bool(re.search('what time',data[0],re.IGNORECASE)):
                count[2][0]+=1
                answer_list = getTextByLabel(paragraph_entity,["DATE","TIME"])
            elif bool(re.search('what year',data[0],re.IGNORECASE) or re.search('what day',data[0],re.IGNORECASE) or re.search('what date',data[0],re.IGNORECASE)):
                count[2][1]+=1
                answer_list = getTextByLabel(paragraph_entity,["DATE"])
            elif bool(re.search('what city',data[0],re.IGNORECASE) or re.search('what country',data[0],re.IGNORECASE)):
                count[2][2]+=1
                answer_list = getTextByLabel(paragraph_entity,["GPE"])
            else:
                count[2][2]+=1
                answer_list = getTextByLabel(paragraph_entity,["FACILITY","PRODUCT","WORK_OF_ART","EVENT","ORG"])
        elif bool(re.search('how',data[0],re.IGNORECASE)):
            if bool(re.search('how much',data[0],re.IGNORECASE)):
                count[3][0]+=1
                answer_list = getTextByLabel(paragraph_entity,["MONEY"])
            if bool(re.search('how many',data[0],re.IGNORECASE)):
                count[3][1]+=1
                answer_list = getTextByLabel(paragraph_entity,["MONEY","QUANTITY","CARDINAL"])
            if bool(re.search('how does',data[0],re.IGNORECASE) or re.search('how was',data[0],re.IGNORECASE)):
                count[3][2]+=1
                answer_list = getTextByLabel(paragraph_entity,["LAW","EVENT","PRODUCT","PERSON"])
            else:
                count[3][3]+=1
                answer_list = getTextByLabel(paragraph_entity,["MONEY","QUANTITY","CARDINAL"])
        elif bool(re.search('when',data[0],re.IGNORECASE)):
            count[4]+=1
            answer_list = getTextByLabel(paragraph_entity,["DATE","TIME"])
        elif bool(re.search('which',data[0],re.IGNORECASE)):
            if bool(re.search('which person',data[0],re.IGNORECASE)):
                count[5][0]+=1
                answer_list = getTextByLabel(paragraph_entity,["PERSON"])
            elif bool(re.search('which time',data[0],re.IGNORECASE)):
                count[5][1]+=1
                answer_list = getTextByLabel(paragraph_entity,["DATE","TIME"])
            elif bool(re.search('which country',data[0],re.IGNORECASE)):
                count[5][2]+=1
                answer_list = getTextByLabel(paragraph_entity,["NORP","ORG"])
            else:
                count[5][3]+=1
                answer_list = getTextByLabel(paragraph_entity,["FACILITY","PRODUCT","WORK_OF_ART","EVENT","ORG"])
        else:
            count[6]+=1
        if len(answer_list)==0:
            useList[1]+=1
            try:
                index = random.randint(0,len(paragraph_entity)-1) 
                answer.append (([str(id_num)+','+paragraph_entity[index].text.replace(",", "")],data[2]))
            except:
                index = random.randint(0,len(data[1])-1)
                answer.append(([str(id_num)+','+data[1][index].replace(",", "")],data[2]))
        else:
            useList[0]+=1
            index = random.randint(0,len(answer_list)-1)
            answer.append (([str(id_num)+','+answer_list[index].replace(",", "")],data[2]))
        id_num +=1
    print("count ",count)
    print("use list ",useList)
    return answer

    

# for line in answer:
#     print(line)
# count  [2198, 279, 422, 156, 563]
# use list  [2757, 861]

In [ ]:
answer = getAnswer(test_data)
# answer = getAnswer(develop_data)

Evaluate function:
print the acurate of answer:

In [ ]:
# def campare(question,answer):
#     if question[4]==str(answer[0]).strip("'").split(',')[1][:-2]:
#         return True
#     else:
#         return False

# def answerAcurate(data_list,answer):
#     data_count = 0
#     correct_count = 0
#     results = map(campare,data_list,answer)
#     for result in results:
#         data_count+=1
#         if result:
#             correct_count +=1
#     return float(correct_count)/data_count

# print(answerAcurate(develop_data,answer))
    

In [ ]:
Write function:

In [ ]:
##Write into csv file
def writeFile(answer):
#     sys.stdout = io.TextIOWrapper(sys.stdout.buffer,encoding='utf8')
    out = open('answer.csv','a',newline='')
    csv_write =csv.writer(out,dialect='excel')
    csv_write.writerow(["id,answer"])
    answerID = 0
    for line in answer:
        try:
            csv_write.writerow(line[0])
        except:
            print("line "+str(answerID)+" cannot write： "+str(line[0]))
        answerID+=1
    out.close()
    
writeFile(answer)
